<a href="https://www.kaggle.com/code/cagkangrsy/anime-recommender-system?scriptVersionId=112546766" target="_blank"><img align="left" alt="Kaggle" title="Open in Kaggle" src="https://kaggle.com/static/images/open-in-kaggle.svg"></a>

# <p style="padding: 20px;background-color:#e88d91;margin:0;color:white;font-family:'Trebuchet MS', sans-serif;font-size:150%;text-align:center;text-shadow: -1px 1px 0 #000,1px 1px 0 #000,1px -1px 0 #000,-1px -1px 0 #000;border-radius: 1000px 1000px;overflow:hidden;font-weight:500">Anime Recommender System</p>

<p style="text-align:center; ">
<img src="https://wallpaperaccess.com/full/39033.png" style='width: 600px; height: 300px;'>
</p>

<p><h1><center><ins>Contributors</ins><br><br>Alihan Demirel<br>Cagkan Gursoy<br>Melisa Gözet</center></h1></p>


**This project is an Hybrid Recommendation System for users that rated different animes. It is based on both user preferences and anime ratings.**

## <ins>**Importing Libraries**<ins>

In [1]:
import pandas as pd
import numpy as np
import random
from mlxtend.frequent_patterns import apriori, association_rules
pd.pandas.set_option('display.max_columns', None)
pd.pandas.set_option('display.width', 300)

This dataset contains information on user preference data from 73,516 users on 12,294 anime. Each user is able to add anime to their completed list and give it a rating and this dataset is a compilation of those ratings.

$\rightarrow$ **anime.csv**

$\bigstar$ **anime_id :** myanimelist.net's unique id identifying an anime.  
$\bigstar$ **name :** full name of anime.  
$\bigstar$ **genre :** comma separated list of genres for this anime.  
$\bigstar$ **type :** movie, TV, OVA, etc.  
$\bigstar$ **episodes :** how many episodes in this show. (1 if movie).  
$\bigstar$ **rating :** average rating out of 10 for this anime.  
$\bigstar$ **members :** number of community members that are in this anime's "group".

$\rightarrow$ **rating.csv**

$\bigstar$ **user_id :** non identifiable randomly generated user id.  
$\bigstar$ **anime_id :** the anime that this user has rated.  
$\bigstar$ **rating :** rating out of 10 this user has assigned (-1 if the user watched it but didn't assign a rating).

In [2]:
anime_ = pd.read_csv("/kaggle/input/anime-recommendations-database/anime.csv")


In [3]:
anime = anime_.copy()

In [4]:
rating_ = pd.read_csv("/kaggle/input/anime-recommendations-database/rating.csv")

In [5]:
rating = rating_.copy()

In [6]:
def general_info (dataframe):
    print(15*"-","Shape",15*"-")
    print(dataframe.shape,"\n")
    print(15*"-","Variable Types",15*"-")
    print(dataframe.info(),"\n")
    print(15*"-","Statistics",15*"-")
    print(dataframe.describe().T,"\n")
    print(15*"-","Null Value",15*"-")
    print(dataframe.isnull().sum(),"\n")

In [7]:
general_info(anime)

--------------- Shape ---------------
(12294, 7) 

--------------- Variable Types ---------------
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 12294 entries, 0 to 12293
Data columns (total 7 columns):
 #   Column    Non-Null Count  Dtype  
---  ------    --------------  -----  
 0   anime_id  12294 non-null  int64  
 1   name      12294 non-null  object 
 2   genre     12232 non-null  object 
 3   type      12269 non-null  object 
 4   episodes  12294 non-null  object 
 5   rating    12064 non-null  float64
 6   members   12294 non-null  int64  
dtypes: float64(1), int64(2), object(4)
memory usage: 672.5+ KB
None 

--------------- Statistics ---------------
            count          mean           std   min      25%       50%       75%        max
anime_id  12294.0  14058.221653  11455.294701  1.00  3484.25  10260.50  24794.50    34527.0
rating    12064.0      6.473902      1.026746  1.67     5.88      6.57      7.18       10.0
members   12294.0  18071.338864  54820.676925  5.00  

In [8]:
general_info(rating)

--------------- Shape ---------------
(7813737, 3) 

--------------- Variable Types ---------------
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 7813737 entries, 0 to 7813736
Data columns (total 3 columns):
 #   Column    Dtype
---  ------    -----
 0   user_id   int64
 1   anime_id  int64
 2   rating    int64
dtypes: int64(3)
memory usage: 178.8 MB
None 

--------------- Statistics ---------------
              count          mean           std  min      25%      50%      75%      max
user_id   7813737.0  36727.956745  20997.946119  1.0  18974.0  36791.0  54757.0  73516.0
anime_id  7813737.0   8909.072104   8883.949636  1.0   1240.0   6213.0  14093.0  34519.0
rating    7813737.0      6.144030      3.727800 -1.0      6.0      7.0      9.0     10.0 

--------------- Null Value ---------------
user_id     0
anime_id    0
rating      0
dtype: int64 



$\nabla$ **The -1 rating value correspnds to no rating given**

In [9]:
rating[rating["rating"] == -1].count()

user_id     1476496
anime_id    1476496
rating      1476496
dtype: int64

$\nabla$  **Anime and rating datasets are merged on ratings,id and names to form a single dataset for analysis.**

In [10]:
anime_ratings = rating.merge(anime[["anime_id", "name"]], how = "inner" , on = "anime_id")

In [11]:
anime_ratings.head()

user_id  anime_id  rating    name
0        1        20      -1  Naruto
1        3        20       8  Naruto
2        5        20       6  Naruto
3        6        20      -1  Naruto
4       10        20      -1  Naruto

$\nabla$ **Ratings are filtered to drop no ratings.**

In [12]:
anime_ratings = anime_ratings[anime_ratings["rating"] >= 0]

$\nabla$ **A pivot table that includes User ID's on index, Anime names on columns and Rating on values is formed.**

In [13]:
anime_df = anime_ratings.pivot_table(index = "user_id", columns = "name", values = "rating")

In [14]:
anime_df.head()

name     &quot;0&quot;  &quot;Aesop&quot; no Ohanashi yori: Ushi to Kaeru, Yokubatta Inu  &quot;Bungaku Shoujo&quot; Kyou no Oyatsu: Hatsukoi  &quot;Bungaku Shoujo&quot; Memoire  &quot;Bungaku Shoujo&quot; Movie  &quot;Eiji&quot;  .hack//G.U. Returner  .hack//G.U. Trilogy  \
user_id                                                                                                                                                                                                                                                                            
1                  NaN                                                NaN                                                               NaN                                   NaN                               NaN               NaN                   NaN                  NaN   
2                  NaN                                                NaN                                                               NaN                                   NaN                               NaN               NaN                   NaN                  NaN   
3                  NaN                                                NaN                                                               NaN                                   NaN                               NaN               NaN                   NaN                  NaN   
5                  NaN                                                NaN                                                               NaN                                   NaN                               NaN               NaN                   NaN                  NaN   
7                  NaN                                                NaN                                                               NaN                                   NaN                               NaN               NaN                   NaN                  NaN   

name     .hack//G.U. Trilogy: Parody Mode  .hack//Gift  .hack//Intermezzo  .hack//Liminality  .hack//Quantum  .hack//Quantum: Sore ike! Bokura no Chimuchimu-chan!!  .hack//Roots  .hack//Sign  .hack//Tasogare no Udewa Densetsu  .hack//Tasogare no Udewa Densetsu: Offline de Aimashou  \
user_id                                                                                                                                                                                                                                                                                     
1                                     NaN          NaN                NaN                NaN             NaN                                                NaN               NaN          NaN                                NaN                                                NaN        
2                                     NaN          NaN                NaN                NaN             NaN                                                NaN               NaN          NaN                                NaN                                                NaN        
3                                     NaN          NaN                NaN                NaN             NaN                                                NaN               NaN          NaN                                NaN                                                NaN        
5                                     NaN          NaN                NaN                NaN             NaN                                                NaN               NaN          NaN                                NaN                                                NaN        
7                                     NaN          NaN                NaN                NaN             NaN                                                NaN               NaN          NaN                                NaN                                                NaN        

name     .hack//The Movie: Sekai no Mukou ni  .hack//Unison  .hack//Ver

$\nabla$ **A random user is chosen to make recommendations.**

In [15]:
random_user = random.choice(anime_df.index)
print(random_user)

55799


$\nabla$ **random_user_df dataframe is defined which includes observations of only the random user.**

In [16]:
random_user_df = anime_df[anime_df.index == random_user]
random_user_df.shape

(1, 9926)

In [17]:
random_user_df.head()

name     &quot;0&quot;  &quot;Aesop&quot; no Ohanashi yori: Ushi to Kaeru, Yokubatta Inu  &quot;Bungaku Shoujo&quot; Kyou no Oyatsu: Hatsukoi  &quot;Bungaku Shoujo&quot; Memoire  &quot;Bungaku Shoujo&quot; Movie  &quot;Eiji&quot;  .hack//G.U. Returner  .hack//G.U. Trilogy  \
user_id                                                                                                                                                                                                                                                                            
55799              NaN                                                NaN                                                               NaN                                   NaN                               NaN               NaN                   NaN                  NaN   

name     .hack//G.U. Trilogy: Parody Mode  .hack//Gift  .hack//Intermezzo  .hack//Liminality  .hack//Quantum  .hack//Quantum: Sore ike! Bokura no Chimuchimu-chan!!  .hack//Roots  .hack//Sign  .hack//Tasogare no Udewa Densetsu  .hack//Tasogare no Udewa Densetsu: Offline de Aimashou  \
user_id                                                                                                                                                                                                                                                                                     
55799                                 NaN          NaN                NaN                NaN             NaN                                                NaN               NaN          NaN                                NaN                                                NaN        

name     .hack//The Movie: Sekai no Mukou ni  .hack//Unison  .hack//Versus: The Thanatos Report  001  009 Re:Cyborg  009-1  009-1: R&amp;B  00:08  07-Ghost  1+2=Paradise  100%  100-man-nen Chikyuu no Tabi: Bander Book  1000-nen Joou: Queen Millennia  1001 Nights  11-nin Iru!  11eyes  \
user_id                                                                                                                                                                                                                                                                                       
55799                                    NaN            NaN                                 NaN  NaN            NaN    NaN             NaN    NaN       NaN           NaN   NaN                                       NaN                             NaN          NaN          NaN     5.0   

name     11eyes Picture Drama  11eyes: Momoiro Genmutan  12-gatsu no Uta  12-sai.  12-sai. 2nd Season  12-sai.: Chicchana Mune no Tokimeki  12-sai.: Chicchana Mune no Tokimeki 2nd Season  15 Bishoujo Hyouryuuki  15 Sonyeon Uju Pyoryugi  1989  20-dai no Heya-hen  2002-nen Harmoni Ondo  \
user_id                                                                                                                                                                                                                                                                                        
55799                     NaN                       NaN              NaN      NaN                 NaN                                  NaN                                             NaN                     NaN                      NaN   NaN                 NaN                    NaN   

name     2005-nen Uchuu no Tabi  2010  2020 Nyeon Ujuui Wonder Kiddy  21 Emon  21 Emon Uchuu ike! Hadashi no Princess  21 Seiki Manga Hajimete Monogatari  21-ji no Onna: Newscaster Katsuragi Miki  2x1  3 Choume no Tama: Onegai! Momo-chan wo Sagashite!!  \
user_id                                                                                                                                                                                                                                                        
55799                       NaN   NaN                            NaN      Na

$\nabla$ **The movies that are rated by random user is stored in a list**

In [18]:
anime_watched = random_user_df.columns[random_user_df.notna().any()].to_list()
anime_watched[0:10]

['11eyes',
 'Absolute Duo',
 'Akagami no Shirayuki-hime',
 'Akatsuki no Yona',
 'Amagi Brilliant Park',
 'Ano Natsu de Matteru',
 'Ano Natsu de Matteru: Bokutachi wa Koukou Saigo no Natsu wo Sugoshinagara, Ano Natsu de Matteiru.',
 'Ao no Exorcist',
 'Blood-C',
 'Boku dake ga Inai Machi']

In [19]:
len(anime_watched)

84

$\nabla$ **The movies that are watched by random user is filtered in the anime_df dataframe.**

In [20]:
anime_watched_df = anime_df[anime_watched]
anime_watched_df.shape

(69600, 84)

$\nabla$ **A new dataframe is created, which contains the information of how many movies each user and selected random user has watched in common.**

In [21]:
anime_movie_count = anime_watched_df.T.notnull().sum()
anime_movie_count = anime_movie_count.reset_index()
anime_movie_count.columns = ["user_id", "anime_count"]
anime_movie_count.head()


user_id  anime_count
0        1            4
1        2            0
2        3           16
3        5           49
4        7           35

In [22]:
anime_movie_count.describe([0.5,0.75,0.90,0.91,0.92,0.93,0.94,0.95,0.96,0.97,0.98,0.99]).T

count          mean           std  min      50%       75%      90%       91%       92%       93%       94%       95%       96%       97%       98%       99%      max
user_id      69600.0  36781.055158  21212.885563  1.0  36811.5  55128.25  66147.1  66879.09  67598.08  68325.07  69062.12  69821.05  70570.04  71303.03  72040.02  72787.01  73516.0
anime_count  69600.0      8.634856     11.115986  0.0      4.0     12.00     24.0     25.00     27.00     29.00     31.00     33.00     36.00     39.00     44.00     50.00     84.0

$\nabla$ **A threshold is defined that describes, what percent of the movies that are rated by random user is watched by other users.**

In [23]:
perc = len(anime_watched) * 25 / 100
users_same_movies = anime_movie_count[anime_movie_count["anime_count"] > perc]["user_id"]
len(users_same_movies)

8329

$\nabla$ **anime_watched_df is filtered so that the ids of users that has anime count above the threshold are selected.**

In [24]:
final_df = anime_watched_df[anime_watched_df.index.isin(users_same_movies)]
final_df.shape

(8329, 84)

In [25]:
final_df.head()

name     11eyes  Absolute Duo  Akagami no Shirayuki-hime  Akatsuki no Yona  Amagi Brilliant Park  Ano Natsu de Matteru  Ano Natsu de Matteru: Bokutachi wa Koukou Saigo no Natsu wo Sugoshinagara, Ano Natsu de Matteiru.  Ao no Exorcist  Blood-C  Boku dake ga Inai Machi  Boruto: Naruto the Movie  \
user_id                                                                                                                                                                                                                                                                                                 
5           NaN           2.0                        NaN               NaN                   6.0                   5.0                                                5.0                                                             4.0      NaN                      NaN                       NaN   
7           NaN           8.0                        NaN               NaN                   NaN                   NaN                                                NaN                                                             NaN      NaN                      9.0                       NaN   
17          NaN           NaN                        NaN               NaN                   8.0                   NaN                                                NaN                                                             NaN      NaN                      8.0                       NaN   
38          1.0           NaN                        NaN               NaN                   NaN                   NaN                                                NaN                                                             7.0      4.0                      NaN                       NaN   
43          9.0           7.0                        NaN               8.0                   NaN                   NaN                                                NaN                                                             7.0      8.0                     10.0                       NaN   

name     Charlotte  Chuunibyou demo Koi ga Shitai!  Chuunibyou demo Koi ga Shitai! Ren  Date A Live II  Dungeon ni Deai wo Motomeru no wa Machigatteiru Darou ka  Elfen Lied  Hai to Gensou no Grimgar  Haikyuu!!  Haikyuu!! Second Season  Hataraku Maou-sama!  High School DxD  High School DxD BorN  \
user_id                                                                                                                                                                                                                                                                                                  
5              NaN                             4.0                                 4.0             2.0                                                6.0                NaN                       NaN        8.0                      9.0                  7.0              2.0                   NaN   
7              7.0                             7.0                                 6.0             8.0                                                7.0                NaN                       7.0        NaN                      NaN                  7.0              6.0                   7.0   
17             5.0                             7.0                                 NaN             6.0                                                NaN                7.0                       NaN        8.0                      9.0                  8.0              8.0                   5.0   
38             NaN                             5.0                                 NaN             NaN                                                NaN                9.0                       7.0       10.0                     10.0                  6.0              5.0                   NaN   
43             NaN                             NaN                                 NaN             NaN                              

$\nabla$ **A new dataframed is defined to find correlations between users.**

In [26]:
corr_df = final_df.T.corr().unstack().sort_values()
corr_df = pd.DataFrame(corr_df, columns=["corr"])
corr_df.index.names = ['user_id_1', 'user_id_2']
corr_df = corr_df.reset_index()
corr_df.head()

user_id_1  user_id_2  corr
0      51696      23895  -1.0
1      71989      58218  -1.0
2       7904      63689  -1.0
3      23895      51696  -1.0
4      32338      70967  -1.0

$\nabla$ **A new dataframe is defined to store users that are significantly correlated to the random user (correlation above the defined threshold).**

In [27]:
top_users = corr_df[(corr_df["user_id_1"] == random_user) & (corr_df["corr"] >= 0.50)][["user_id_2", "corr"]].reset_index(drop=True)
top_users = top_users.sort_values(by='corr', ascending=False)
top_users.rename(columns={"user_id_2": "user_id"}, inplace=True)
top_users.shape

(246, 2)

In [28]:
top_users.head()

user_id      corr
245    55799  1.000000
244    70693  0.736080
243     9131  0.724506
242    42361  0.715880
241    46985  0.714411

$\nabla$ **top_users dataframe is merged with anime_ratings to get  anime_id and ratings**

In [29]:
top_users_ratings = top_users.merge(anime_ratings[["user_id", "anime_id", "rating"]], how='inner')
top_users_ratings = top_users_ratings[top_users_ratings["user_id"] != random_user]
top_users_ratings["user_id"].unique()
top_users_ratings.head()

user_id     corr  anime_id  rating
84    70693  0.73608       356       9
85    70693  0.73608      2993       7
86    70693  0.73608      4214       7
87    70693  0.73608      4224       9
88    70693  0.73608      6547       9

$\nabla$ **A new variable is defined as the product of correlation and rating. This includes the correlation effect on the user's ratings.**

In [30]:
top_users_ratings['weighted_rating'] = top_users_ratings['corr'] * top_users_ratings['rating']
top_users_ratings.head()

user_id     corr  anime_id  rating  weighted_rating
84    70693  0.73608       356       9         6.624719
85    70693  0.73608      2993       7         5.152559
86    70693  0.73608      4214       7         5.152559
87    70693  0.73608      4224       9         6.624719
88    70693  0.73608      6547       9         6.624719

$\nabla$ **A dataframe is defined that includes Anime IDs and weighted rating averages.**

In [31]:
recommendation_df = top_users_ratings.groupby('anime_id').agg({"weighted_rating": "mean"})
recommendation_df = recommendation_df.reset_index()
recommendation_df.head()

anime_id  weighted_rating
0         1         4.655258
1         5         4.484032
2         6         4.597092
3         7         3.672948
4         8         3.167045

$\nabla$ **recommendation_df is filtered to get animes above a certain rating threshold.**

In [32]:
recommendation_df[recommendation_df["weighted_rating"] > 5]
movies_to_be_recommend = recommendation_df[recommendation_df["weighted_rating"] > 5].sort_values("weighted_rating", ascending=False)

$\nabla$ **Lastly, 10 recommendations are made for the selected random user**

In [33]:
recommendation = movies_to_be_recommend.merge(anime[["anime_id", "name","rating"]])[["name","rating"]][0:10]
recommendation

name  rating
0                                Doukyuusei (Movie)    8.53
1      Kara no Kyoukai: Mirai Fukuin - Manner Movie    6.17
2                        Gall Force 3: Stardust War    6.63
3                               Akai Koudan Zillion    6.90
4                    Choujin Densetsu Urotsukidouji    6.34
5                                Freedom Previsited    6.76
6                         Gall Force 2: Destruction    6.65
7                       Gall Force 1: Eternal Story    6.70
8  Youkai Watch Movie 1: Tanjou no Himitsu da Nyan!    7.48
9                   Inazuma Eleven Go: Chrono Stone    7.45

$\nabla$ **Recommendations are exported to a .csv file**

In [34]:
recommendation.to_csv("recommendation.csv",index=False)